In [ ]:
!pip install internetarchive moviepy pandas bs4 tqdm

In [ ]:
import pandas as pd
from uuid import uuid4
from datetime import datetime
from bs4 import BeautifulSoup
import internetarchive as ia

from moviepy.editor import *
import glob
import os

import zipfile
import os
import re
import shutil
import glob
from tqdm import tqdm

In [ ]:
# Google Drive benutzen um Dateien permanent zu speichern

from google.colab import drive
drive.mount('/mnt/drive')

google_drive_path = "/mnt/drive/MyDrive/MasterArbeitDaten"

Drive already mounted at /mnt/drive; to attempt to forcibly remount, call drive.mount("/mnt/drive", force_remount=True).


In [ ]:
file_links = []

# Identifier of the Archive.org collection
collection_identifier = "schwurbel-archiv"

# Search for items in the collection
items = ia.search_items('collection:' + collection_identifier)

data = []

# Iterate over the items
for item in items:
    data.append({
        "ID": uuid4(),
        "identifier": item['identifier'],
        "status": "Added",
        "downloaded": "",
        "group_name": "",
        "crawl_data": ""
    })

df = pd.DataFrame.from_dict(data)
df.to_csv(f"{google_drive_path}/2023-07-06-Schwurbelarchiv-Liste.csv")

## Import aus CSV

In [ ]:
df = pd.read_csv(f"{google_drive_path}/GruppenAuswahlDokus.csv", sep=';', encoding='utf-8')


df['status'] = "Added"
df.to_csv(f"{google_drive_path}/GruppenAuswahlDokus.csv")
df.head()

item  path                                 name  \
0  schwurbelarchiv-11I2gdLfJW   NaN  KenFM Ken Jebsen Fanchat Diskussion   
1  schwurbelarchiv-4R1BV8YA4t   NaN                KenFM 🎙 Podcast-Kanal   
2  schwurbelarchiv-8AortHrNPy   NaN                            COMPACTTV   
3  schwurbelarchiv-9T0Kpu6phZ   NaN    kla.TV - Die anderen Nachrichten!   
4  schwurbelarchiv-APJu23H8ht   NaN             Oliver Janich öffentlich   

       date          ts status  
0   3122020  1606950000  Added  
1   3042020  1585864800  Added  
2  22112020  1605999600  Added  
3  23082020  1598133600  Added  
4  23082020  1598133600  Added

1. Finde alle Videos, extrahiere Ton und Bild.
2. Lösche Videodateien.

In [ ]:
def update_status(index, status):
    df.at[index, 'status'] = status
    df.to_csv(google_drive_path + 'GruppenAuswahlDokus (2).csv', index=False)  # Save the DataFrame to a CSV file

In [ ]:
import cv2

def extract_first_frame(video_path, output_dir):
    # Check if the video file exists
    if not os.path.exists(video_path):
        print(f"File not found: {video_path}")
        return

    # Open the video file
    video = cv2.VideoCapture(video_path)

    # Read the first frame
    success, frame = video.read()

    if success:
        base_name = os.path.splitext(os.path.basename(video_path))[0]
        image_file_name = base_name + '.png'
        image_path = os.path.join(output_dir, image_file_name)

        # Save the first frame as an image
        cv2.imwrite(image_path, frame)

        print(f"Saved first frame to {image_path}")
    else:
        print("Failed to read the first frame from the video.")

    # Release the video capture object
    video.release()

def extract_audio(file_path, output_dir):
    # print(file_path)
    # Load the video file
    video = VideoFileClip(file_path)

    # Extract the audio from the video file
    audio = video.audio

    if audio is not None:

      sampling_rate =  audio.fps

      # Get the current suffix
      current_suffix = file_path.split(".")[-1]

      # Replace the current suffix with "mp3"
      new_filename = file_path.replace(current_suffix, "mp3")
      new_filename = os.path.basename(new_filename)
      new_filename = f"{output_dir}/{new_filename}"

      # Save the audio to a file
      audio.write_audiofile(new_filename)

    # Close the video file
    video.close()

def process_videos(directory_path, output_dir):
    # Construct the search pattern
    print(directory_path)
    search_pattern = os.path.join(directory_path, '**', '*.mp4')

     print(glob.glob(search_pattern, recursive=True))

    # Find all .mp4 files in the directory and its subdirectories
    for video_path in glob.glob(search_pattern, recursive=True):
      try:
        print(f"Extracting Audio from {video_path}")
        extract_audio(video_path, output_dir)
        extract_first_frame(video_path, output_dir)
        delete_videos(video_path)
      except Exception as e:
        print(f"Error processing {video_path}: {e}")
        continue

def delete_videos(video_path):
    # Check if the file exists
    if os.path.exists(video_path):
        # Delete the file
        os.remove(video_path)
        print(f"Deleted: {video_path}")
    else:
        # File does not exist
        print(f"File not found: {video_path}")

In [ ]:
print(df)

                          item  path  \
0   schwurbelarchiv-11I2gdLfJW   NaN   
1   schwurbelarchiv-4R1BV8YA4t   NaN   
2   schwurbelarchiv-8AortHrNPy   NaN   
3   schwurbelarchiv-9T0Kpu6phZ   NaN   
4   schwurbelarchiv-APJu23H8ht   NaN   
..                         ...   ...   
71  schwurbelarchiv-RC14tt1MkL   NaN   
72  schwurbelarchiv-jC3iFLyc95   NaN   
73  schwurbelarchiv-sKnYL5eu52   NaN   
74  schwurbelarchiv-MTPWDClQaz   NaN   
75  schwurbelarchiv-wQKfoNosUQ   NaN   

                                                 name      date          ts  \
0                 KenFM Ken Jebsen Fanchat Diskussion   3122020  1606950000   
1                               KenFM 🎙 Podcast-Kanal   3042020  1585864800   
2                                           COMPACTTV  22112020  1605999600   
3                   kla.TV - Die anderen Nachrichten!  23082020  1598133600   
4                            Oliver Janich öffentlich  23082020  1598133600   
..                                           

In [ ]:
df = df.drop ("id")
print(df)

In [ ]:
def scrape_content(filepath):
  # Read the HTML file
  with open(filepath, 'r', encoding='utf-8') as file:
      html_content = file.read()

  # Create a Beautiful Soup object
  soup = BeautifulSoup(html_content, 'lxml')

  messages = soup.find_all('div', class_='message')
  data = []

  # Iterate over the messages
  for message_div in messages:
      from_name_div = message_div.find('div', class_='from_name')
      if not from_name_div:
          #print(message_div)
          continue

      from_name = from_name_div.get_text(strip=True)
      forwarded_div = message_div.find('div', class_='forwarded body')

      forwarded_from_name = ""
      forwarded_message_text = ""
      forwarded_message_photo = ""
      forwarded_video_duration = ""
      if forwarded_div:
          forwarded_from_name_div = forwarded_div.find('div', class_='from_name')
          forwarded_from_name = forwarded_from_name_div.get_text(strip=True).replace(forwarded_from_name_div.find('span', class_='details').get_text(strip=True), '')

          message_text_div = forwarded_div.find('div', class_='text')
          forwarded_message_text = ''.join(str(child) for child in message_text_div.contents) if message_text_div else ""

          message_photo = forwarded_div.find('img')
          forwarded_message_photo = message_photo['src'] if message_photo else ""

          video_duration_div = forwarded_div.find('div', class_='video_duration')
          forwarded_video_duration = video_duration_div.get_text(strip=True) if video_duration_div else ""


      message_text_div = message_div.find('div', class_='text')
      message_text = ""
      message_photo = ""
      video_duration = ""
      if message_text_div:
          message_text = ''.join(str(child) for child in message_text_div.contents) if message_text_div else ""

          message_photo = message_div.find('img')
          message_photo = message_photo['src'] if message_photo else ""

          video_duration_div = message_div.find('div', class_='video_duration')
          video_duration = video_duration_div.get_text(strip=True) if video_duration_div else ""

      date_element = message_div.find('div', class_='pull_right date details')
      datetime_value = date_element['title']
      datetime_object = datetime.strptime(datetime_value, '%d.%m.%Y %H:%M:%S')

      # Append the extracted data to the list
      data.append({
          'ID': uuid4(),
          'From Name': from_name,
          'Datetime': datetime_object,
          'Message Text': message_text,
          'Photo': message_photo,
          'Video Duration': video_duration,
          'Forwarded From Name': forwarded_from_name,
          'Forwarded Message Text': forwarded_message_text,
          'Forwarded Photo': forwarded_message_photo,
          'Forwarded Video Duration': forwarded_video_duration
      })

  # Create a pandas DataFrame from the extracted data
  data_df = pd.DataFrame(data)

  # Speichern des DataFrames als CSV-Datei
  data_df.to_csv('messages_df.csv', index=False)
  return data_df

In [ ]:
# Directory for saving individual CSV files
output_dir = google_drive_path
# Ensure the output directory exists
if not os.path.exists(output_dir):
    os.makedirs(output_dir)


# Option: Nur eine Zeile zum Testen: df.sample(1).iterrows():
for index, row in tqdm((df).iterrows(), desc="Downloading files"):

    download_path = "/content/downloads"
    if os.path.exists(download_path):
        shutil.rmtree(download_path)
    os.makedirs(download_path)

    raw_data_path = "/content/raw"
    if os.path.exists(raw_data_path):
        shutil.rmtree(raw_data_path)
    os.makedirs(raw_data_path)

    identifier = row['item']
    group_dir = f"{output_dir}/{identifier}"

    if os.path.exists(group_dir):
      print(f"Folder for {identifier} already exists, skipping download.")
      continue


    item = ia.get_item(identifier)
    print(item)

    # Get group name
    name = item.metadata['title']

    # Extract the name
    name_pattern = r'„(.*?)“'
    name_match = re.search(name_pattern, name)
    group_name = name_match.group(1) if name_match else ""
    df.at[index, 'group_name'] = group_name

    # Extract the date
    date_pattern = r'vom (\d{2}\.\d{2}\.\d{4})'
    date_match = re.search(date_pattern, name)
    crawl_date = date_match.group(1) if date_match else ""
    # Convert the crawl_date_str to a datetime object
    crawl_date = datetime.strptime(crawl_date, "%d.%m.%Y")

    # Update the 'crawl_date' column in the DataFrame
    df.at[index, 'crawl_date'] = crawl_date

    print(f"Working on {identifier} -- {group_name}")

    download_files = []
    for f in ia.get_files(identifier):
      if f.format == "ZIP":
        download_files.append(f)
        print(f"Downloading {f.name}")
        f.download(destdir = download_path)

    for file in download_files:
        print(f"Extracting {f.name}")
        with zipfile.ZipFile(f"{download_path}/{file.name}") as zip:
          zip.extractall(raw_data_path)



    group_dir = f"{output_dir}/{identifier}"
    os.makedirs(group_dir)

    # Finden aller messages*.html Dateien im Verzeichnis
    html_files = glob.glob(f"{raw_data_path}/messages*.html")

    # Liste, um die DataFrames zu speichern
    df_list = []

    # Verarbeiten jeder Datei und Hinzufügen des Ergebnisses zur Liste
    for file in html_files:
        # Construct a unique output filename for each HTML file
        base_name = os.path.splitext(os.path.basename(file))[0]
        output_csv = os.path.join(output_dir, f"{base_name}_{row['item']}.csv")

        # Process the HTML file and save the result in the specified CSV file
        df_specified = scrape_content(file, output_csv)

        print(f"Processing messages: {file}")
        df_specified = scrape_content(file)
        df_list.append(df_specified)

    # Zusammenführen aller DataFrames zu einem einzigen DataFrame
    merged_df = pd.concat(df_list, ignore_index=True)

    # Erstellen eines dynamischen Dateinamens basierend auf dem 'item'
    csv_file_path = f"{group_dir}/merged_messages.csv"
    merged_df.to_csv(csv_file_path, index=False)

    print(f"Die Datei {csv_file_path} wurde erfolgreich gespeichert.")

    print("Extracting Audio.")

    # Finds all Videos, processes them: 1) Extracts Audio 2) Extracts first frame as image 3) Deletes the video
    # to save space.
    audio_dir = f"{group_dir}/audio"
    os.makedirs(audio_dir)
    process_videos(raw_data_path, audio_dir)


print("Processing complete.")

Folder for schwurbelarchiv-11I2gdLfJW already exists, skipping download.
Folder for schwurbelarchiv-4R1BV8YA4t already exists, skipping download.
Folder for schwurbelarchiv-8AortHrNPy already exists, skipping download.
Folder for schwurbelarchiv-9T0Kpu6phZ already exists, skipping download.
Folder for schwurbelarchiv-APJu23H8ht already exists, skipping download.
Folder for schwurbelarchiv-EHCO11xzLu already exists, skipping download.
Folder for schwurbelarchiv-KesheeJe5E already exists, skipping download.
Folder for schwurbelarchiv-MLZQrayr99 already exists, skipping download.
Folder for schwurbelarchiv-OG223gfZo4 already exists, skipping download.
Folder for schwurbelarchiv-QDHQA6B3qC already exists, skipping download.
Folder for schwurbelarchiv-UJ8kah9CZj already exists, skipping download.
Folder for schwurbelarchiv-WRyhi5Knwj already exists, skipping download.
Folder for schwurbelarchiv-eZv2No2KQs already exists, skipping download.
Folder for schwurbelarchiv-g6Sbm9HSmG already exist

MoviePy - Writing audio in /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-Ot4ODB43LA/audio/Bildschirmvideo aufnehmen 2020-08-08 um 20.52.15.mp3



chunk:  99%|█████████▉| 8299/8401 [00:04<00:00, 2119.33it/s, now=None]

MoviePy - Done.


Saved first frame to /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-Ot4ODB43LA/audio/Bildschirmvideo aufnehmen 2020-08-08 um 20.52.15.png
Deleted: /content/raw/video_files/Bildschirmvideo aufnehmen 2020-08-08 um 20.52.15.mp4
Extracting Audio from /content/raw/video_files/Der Wahnsinn geht weiter (online-video-cutter.com).mp4
MoviePy - Writing audio in /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-Ot4ODB43LA/audio/Der Wahnsinn geht weiter (online-video-cutter.com).mp3


...

MoviePy - Done.
Saved first frame to /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-eITHweQ1Yi/audio/STANDPUNKTE_•_Coronavirus_Irreführung_bei_den_Fallzahlen_nun_belegt.png
Deleted: /content/raw/video_files/STANDPUNKTE_•_Coronavirus_Irreführung_bei_den_Fallzahlen_nun_belegt.mp4
Extracting Audio from /content/raw/video_files/Demoaufruf_Kündigt_Airbase_Ramstein_JETZT_30.05.2020_11.134.mp4
MoviePy - Writing audio in /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-eITHweQ1Yi/audio/Demoaufruf_Kündigt_Airbase_Ramstein_JETZT_30.05.2020_11.134.mp3



chunk:  99%|█████████▉| 6435/6471 [00:04<00:00, 1489.60it/s, now=None]

MoviePy - Done.
Saved first frame to /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-eITHweQ1Yi/audio/Demoaufruf_Kündigt_Airbase_Ramstein_JETZT_30.05.2020_11.134.png
Deleted: /content/raw/video_files/Demoaufruf_Kündigt_Airbase_Ramstein_JETZT_30.05.2020_11.134.mp4
Extracting Audio from /content/raw/video_files/video_2@06-06-2020_23-37-06.mp4
MoviePy - Writing audio in /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-eITHweQ1Yi/audio/video_2@06-06-2020_23-37-06.mp3



chunk: 100%|█████████▉| 404/406 [00:00<00:00, 1310.78it/s, now=None]

MoviePy - Done.
Saved first frame to /mnt/drive/MyDrive/MasterArbeitDaten/schwurbelarchiv-eITHweQ1Yi/audio/video_2@06-06-2020_23-37-06.png
Deleted: /content/raw/video_files/video_2@06-06-2020_23-37-06.mp4
Folder for schwurbelarchiv-glzorWfNfL already exists, skipping download.
Folder for schwurbelarchiv-wt6PQuPp10 already exists, skipping download.
Folder for schwurbelarchiv-wxJECPHb6O already exists, skipping download.
Folder for schwurbelarchiv-zAxIIAdupk already exists, skipping download.
Folder for schwurbelarchiv-HbdicJbU5D already exists, skipping download.
Folder for schwurbelarchiv-IkjkLl8t4d already exists, skipping download.
Folder for schwurbelarchiv-LmKd4mfk9b already exists, skipping download.
Folder for schwurbelarchiv-Y3YKKrSYYx already exists, skipping download.
Item(identifier='schwurbelarchiv-YQzIe0zCyP')
Working on schwurbelarchiv-YQzIe0zCyP -- KenFM 🎙 Podcast
